In [1]:
from pyomo.environ import *
from pyomo.opt import *
opt = solvers.SolverFactory("glpk")

In [2]:
b = {'F1':50,
     'F2':40,
     'DC':0,
     'W1':-30,
     'W2':-60}

C = {('F1','F2'):200,
     ('F1','DC'):400,
     ('F1','W1'):100,
     ('F2','DC'):300,
     ('DC','W1'):100,
     ('DC','W2'):200,
     ('W1','W2'):200,
     ('W2','W1'):100}

U = {('DC','W2'):40,
     ('F1','W1'):20,
     ('W2','W1'):20}

N = list(b.keys())
A = list(C.keys())
V = list(U.keys())

In [3]:
model = ConcreteModel()
model.f = Var(A, within=NonNegativeReals)

def flow_rule(model, n):
    InFlow  = sum(model.f[i,j] for (i,j) in A if j==n)
    OutFlow = sum(model.f[i,j] for (i,j) in A if i==n)
    return InFlow + b[n] == OutFlow
    
model.flow = Constraint(N, rule=flow_rule)

def capacity_rule(model, i, j):
    return U[i,j] >= model.f[i,j]

model.capacity = Constraint(V, rule=capacity_rule)

model.cost = Objective(expr = sum(model.f[a]*C[a] for a in A), sense=minimize)

In [4]:
model.dual = Suffix(direction=Suffix.IMPORT)
results = opt.solve(model)
model.f.get_values()

{('DC', 'W1'): 30.0,
 ('DC', 'W2'): 40.0,
 ('F1', 'DC'): 30.0,
 ('F1', 'F2'): 0.0,
 ('F1', 'W1'): 20.0,
 ('F2', 'DC'): 40.0,
 ('W1', 'W2'): 20.0,
 ('W2', 'W1'): 0.0}

In [5]:
for (i,j) in V:
    print ((i,j), model.dual[model.capacity[(i,j)]])

('DC', 'W2') -100.0
('F1', 'W1') -400.0
('W2', 'W1') 0.0
